# Outros exemplos de classificação

## Categorizando gênero e idade

Vamos testar com o seguinte modelo, que promete categorizar idade e gênero de uma voz: https://huggingface.co/audeering/wav2vec2-large-robust-24-ft-age-gender

In [1]:
from datasets import load_dataset

nome_dataset = "google/fleurs"
lingua_dataset = "en_us"
dados = load_dataset(nome_dataset, name=lingua_dataset, split='train', streaming=True)
dados

/home/juliano/.cache/pypoetry/virtualenvs/ias_para_imagens,_áudio_e_vídeo_no_hugging-hFrc_0yz-py3.11/lib/python3.11/site-packages/datasets/load.py:1461: FutureWarning: The repository for google/fleurs contains custom code which must be executed to correctly load the dataset. You can inspect the repository content at https://hf.co/datasets/google/fleurs
You can avoid this message in future by passing the argument `trust_remote_code=True`.
Passing `trust_remote_code=True` will be mandatory to load this dataset from the next major release of `datasets`.
  warnings.warn(


IterableDataset({
    features: ['id', 'num_samples', 'path', 'audio', 'transcription', 'raw_transcription', 'gender', 'lang_id', 'language', 'lang_group_id'],
    n_shards: 1
})

In [2]:
from transformers import pipeline

modelo = 'audeering/wav2vec2-large-robust-24-ft-age-gender'
classificador = pipeline('audio-classification', model=modelo)
print(classificador.feature_extractor.sampling_rate)

Some weights of Wav2Vec2ForSequenceClassification were not initialized from the model checkpoint at audeering/wav2vec2-large-robust-24-ft-age-gender and are newly initialized: ['classifier.bias', 'classifier.weight', 'projector.bias', 'projector.weight', 'wav2vec2.encoder.pos_conv_embed.conv.parametrizations.weight.original0', 'wav2vec2.encoder.pos_conv_embed.conv.parametrizations.weight.original1']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


16000


In [3]:
import IPython

for linha in dados.take(5):
    audio = linha['audio']
    predicao = classificador(audio.copy())  # Importante porque o dicionário é modificado
    print(predicao)
    display(IPython.display.Audio(data=audio['array'], rate=audio['sampling_rate']))

[{'score': 0.33387747406959534, 'label': 'child'}, {'score': 0.3333945870399475, 'label': 'female'}, {'score': 0.33272793889045715, 'label': 'male'}]


[{'score': 0.34161368012428284, 'label': 'female'}, {'score': 0.3306569457054138, 'label': 'child'}, {'score': 0.3277294337749481, 'label': 'male'}]


[{'score': 0.3351593613624573, 'label': 'male'}, {'score': 0.3327524662017822, 'label': 'female'}, {'score': 0.3320882022380829, 'label': 'child'}]


[{'score': 0.3364161252975464, 'label': 'male'}, {'score': 0.33482447266578674, 'label': 'female'}, {'score': 0.32875943183898926, 'label': 'child'}]


[{'score': 0.3442152440547943, 'label': 'female'}, {'score': 0.3306393325328827, 'label': 'child'}, {'score': 0.3251454830169678, 'label': 'male'}]


Algo não parece certo com a predição.. como ajustar?

Vamos usar o código descrito no card do modelo no Hugging Face: https://huggingface.co/audeering/wav2vec2-large-robust-24-ft-age-gender

In [4]:
import numpy as np
import torch
import torch.nn as nn
from transformers import Wav2Vec2Processor
from transformers.models.wav2vec2.modeling_wav2vec2 import (
    Wav2Vec2Model,
    Wav2Vec2PreTrainedModel,
)


class ModelHead(nn.Module):
    r"""Classification head."""

    def __init__(self, config, num_labels):

        super().__init__()

        self.dense = nn.Linear(config.hidden_size, config.hidden_size)
        self.dropout = nn.Dropout(config.final_dropout)
        self.out_proj = nn.Linear(config.hidden_size, num_labels)

    def forward(self, features, **kwargs):

        x = features
        x = self.dropout(x)
        x = self.dense(x)
        x = torch.tanh(x)
        x = self.dropout(x)
        x = self.out_proj(x)

        return x


class AgeGenderModel(Wav2Vec2PreTrainedModel):
    r"""Speech emotion classifier."""

    def __init__(self, config):

        super().__init__(config)

        self.config = config
        self.wav2vec2 = Wav2Vec2Model(config)
        self.age = ModelHead(config, 1)
        self.gender = ModelHead(config, 3)
        self.init_weights()

    def forward(
            self,
            input_values,
    ):

        outputs = self.wav2vec2(input_values)
        hidden_states = outputs[0]
        hidden_states = torch.mean(hidden_states, dim=1)
        logits_age = self.age(hidden_states)
        logits_gender = torch.softmax(self.gender(hidden_states), dim=1)

        return hidden_states, logits_age, logits_gender

In [5]:
def process_func(
    model,
    processor,
    x: np.ndarray,
    sampling_rate: int,
    embeddings: bool = False,
    device: str = 'cpu',
) -> np.ndarray:
    r"""Predict age and gender or extract embeddings from raw audio signal."""

    # run through processor to normalize signal
    # always returns a batch, so we just get the first entry
    # then we put it on the device
    y = processor(x, sampling_rate=sampling_rate)
    y = y['input_values'][0]
    y = y.reshape(1, -1)
    y = torch.from_numpy(y).to(device)

    # run through model
    with torch.no_grad():
        y = model(y)
        if embeddings:
            y = y[0]
        else:
            y = torch.hstack([y[1], y[2]])

    # convert to numpy
    y = y.detach().cpu().numpy()

    return y

In [6]:
nome_modelo = 'audeering/wav2vec2-large-robust-24-ft-age-gender'

processador = Wav2Vec2Processor.from_pretrained(nome_modelo)
modelo = AgeGenderModel.from_pretrained(nome_modelo)

Some weights of AgeGenderModel were not initialized from the model checkpoint at audeering/wav2vec2-large-robust-24-ft-age-gender and are newly initialized: ['wav2vec2.encoder.pos_conv_embed.conv.parametrizations.weight.original0', 'wav2vec2.encoder.pos_conv_embed.conv.parametrizations.weight.original1']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [7]:
def exibe_predicao(predicao):
    idade = predicao[0][0] * 100
    prob_mulher = predicao[0][1] * 100
    prob_homem = predicao[0][2] * 100
    prob_crianca = predicao[0][3] * 100
    print(f'Idade: {idade:.2f}')
    print(f'Pessoa inferida:\n{prob_mulher:.2f}% Mulher\n{prob_homem:.2f}% Homem\n{prob_crianca:.2f}% Criança')


for linha in dados.take(5):
    x = linha['audio']['array']
    sampling_rate = linha['audio']['sampling_rate']
    predicao = process_func(model=modelo, processor=processador, x=x, sampling_rate=sampling_rate)
    exibe_predicao(predicao)
    display(IPython.display.Audio(data=x, rate=sampling_rate))

Idade: 27.90
Pessoa inferida:
97.66% Mulher
1.37% Homem
0.97% Criança


Idade: 39.59
Pessoa inferida:
0.51% Mulher
99.45% Homem
0.03% Criança


Idade: 25.27
Pessoa inferida:
99.43% Mulher
0.44% Homem
0.13% Criança


Idade: 54.73
Pessoa inferida:
52.67% Mulher
47.31% Homem
0.02% Criança


Idade: 63.15
Pessoa inferida:
0.07% Mulher
99.92% Homem
0.01% Criança


### Testando agora com gravação

In [18]:
import sounddevice as sd

duracao = 10
taxa_amostragem = 16000
tamanho_vetor = int(duracao * taxa_amostragem)

gravacao = sd.rec(tamanho_vetor, samplerate=taxa_amostragem, channels=1).ravel()
sd.wait()

In [19]:
IPython.display.Audio(data=gravacao, rate=taxa_amostragem)

In [34]:
predicao = process_func(model=modelo, processor=processador, x=gravacao, sampling_rate=taxa_amostragem)
exibe_predicao(predicao)

Idade: 45.59
Pessoa inferida:
25.24% Mulher
61.74% Homem
13.02% Criança


## Classificação *zero-shot*

Com alguns modelos, podemos fazer classificação *zero-shot*. Isso significa que nós mesmos podemos passar as classes para o modelo classificar dentre elas.

Vamos ver um exemplo simples com o mesmo Dataset visto na aula anterior: https://huggingface.co/datasets/ashraq/esc50

In [1]:
from datasets import load_dataset

dados = load_dataset('ashraq/esc50', split='train[:10]')  # Apenas as 10 primeiras linhas
for linha in dados:
    print(linha)

Repo card metadata block was not found. Setting CardData to empty.


{'filename': '1-100032-A-0.wav', 'fold': 1, 'target': 0, 'category': 'dog', 'esc10': True, 'src_file': 100032, 'take': 'A', 'audio': {'path': None, 'array': array([0., 0., 0., ..., 0., 0., 0.]), 'sampling_rate': 44100}}
{'filename': '1-100038-A-14.wav', 'fold': 1, 'target': 14, 'category': 'chirping_birds', 'esc10': False, 'src_file': 100038, 'take': 'A', 'audio': {'path': None, 'array': array([-0.01184082, -0.10336304, -0.14141846, ...,  0.06985474,
        0.04049683,  0.00274658]), 'sampling_rate': 44100}}
{'filename': '1-100210-A-36.wav', 'fold': 1, 'target': 36, 'category': 'vacuum_cleaner', 'esc10': False, 'src_file': 100210, 'take': 'A', 'audio': {'path': None, 'array': array([-0.00695801, -0.01251221, -0.01126099, ...,  0.215271  ,
       -0.00875854, -0.28903198]), 'sampling_rate': 44100}}
{'filename': '1-100210-B-36.wav', 'fold': 1, 'target': 36, 'category': 'vacuum_cleaner', 'esc10': False, 'src_file': 100210, 'take': 'B', 'audio': {'path': None, 'array': array([0.53897095, 

In [2]:
from transformers import pipeline

modelo = 'laion/clap-htsat-fused'
classificador = pipeline("zero-shot-audio-classification", model=modelo)
print(classificador.feature_extractor.sampling_rate)

48000


In [3]:
from datasets import Audio

dados = dados.cast_column("audio", Audio(sampling_rate=48000))

In [4]:
labels = [
    'Sound of a dog',
    'Sound of birds',
    'Sound of a cat',
    'Sound of a cow',
    'Sound of a vacuum cleaner'
]

for linha in dados:
    categoria = linha['category']
    predicao = classificador(linha['audio']['array'], candidate_labels=labels)
    print(f'Tipo: {categoria}\nPredição: {predicao[0]["label"]} (score: {predicao[0]["score"]})')
    print('-----')

Tipo: dog
Predição: Sound of a dog (score: 0.9988256096839905)
-----
Tipo: chirping_birds
Predição: Sound of birds (score: 0.9992444515228271)
-----
Tipo: vacuum_cleaner
Predição: Sound of a vacuum cleaner (score: 0.9987397789955139)
-----
Tipo: vacuum_cleaner
Predição: Sound of a vacuum cleaner (score: 0.9998911619186401)
-----
Tipo: thunderstorm
Predição: Sound of a cow (score: 0.812597930431366)
-----
Tipo: thunderstorm
Predição: Sound of a cow (score: 0.8609116673469543)
-----
Tipo: door_wood_knock
Predição: Sound of a cow (score: 0.9805388450622559)
-----
Tipo: can_opening
Predição: Sound of a dog (score: 0.8917930722236633)
-----
Tipo: crow
Predição: Sound of birds (score: 0.729194700717926)
-----
Tipo: door_wood_knock
Predição: Sound of a cow (score: 0.6846061944961548)
-----


Modelos desse tipo poderiam ser usados para diversas outras aplicações: 
- Comandos de voz (Ex: "Ok Google", "Alexa")
- Detectar padrões sonoros (respiração de pacientes em UTI, sons na rua para segurança pública, ...)